# TP 5 : Modules mathématiques et Networkx en particulier

## 1 - Utiliser des modules

Nous avons déjà vu, dans le premier TP, comment utiliser une fonction contenue dans un *module*, c'est-à-dire une collection de programmes écrits par quelqu'un d'autre. Mais nous allons explorer ça un peu plus avec le module `math`, qui donne accès à des fonctionnalités type calculatrice (sinus et cosinus, etc).

Rappelons comment on importe une fonction isolée :

In [ ]:
from math import sqrt # sqrt pour 'square root', racine carrée

In [ ]:
sqrt(2)

On peut aussi changer le nom si on préfère :

In [ ]:
from math import sqrt as racine

In [ ]:
racine(2)

Il est possible d'utiliser `from math import *` pour **tout** importer, mais il n'est vraiment pas recommandé de faire ça. (Il y a bien des raisons, mais imaginez déjà que le module `math` contienne une fonction qui s'appelle exactement comme l'une des vôtres, sans que vous le sachiez...)

On préfèrera importer le module lui-même en faisant :

In [ ]:
import math

In [ ]:
math.sqrt(2)

Pour voir toutes les fonctions du module `math`, maintenant qu'il est importé, tapez `math.` avec le point et utilisez la touche TAB.

In [ ]:
math.pi

Pour les plus paresseux, on peut également abréger le nom du module :

In [ ]:
import math as m

In [ ]:
m.sin( m.pi )

L'écriture ci-dessus indique $1.22 \cdot 10^{-16}$, qui est vraiment très proche de 0. Le nombre pi tel que le définit le module `math` est un "float", et la fonction sinus de ce module renvoie des floats également, qui sont des nombres approchés.


## 2 - Les graphes avec Networkx

Nous allons regarder de près un module qui permet de travailler avec les graphes, ce qui nous donnera accès à de nombreux algorithmes déjà prêts à l'emploi. Et ceci, même si les problèmes qui nous intéressent ne semble pas *a priori* relever des graphes.

Mathématiquement, un *graphe* est donné par un ensemble $S$ dont les éléments s'appellent les sommets, et par un ensemble $A$ dont les éléments sont des paires $\{u, v\}$, avec $u, v\in S$ et $u\ne v$, que l'on appelle les arêtes. (Pour nous, $S$ sera en général fini et composé de nombres entiers.)

On peut représenter un graphe en faisant un dessin simple : un point pour chaque sommet, et un segment pour chaque arête. Le dessin nous aide fortement à réfléchir aux propriétés du graphe. Par contre **attention** un graphe n'est pas un dessin, et il y a d'ailleurs plusieurs dessins possibles.

Il y a différents modules en Python pour travailler avec les graphes, et nous allons voir networkx:


In [ ]:
import networkx as nx  # on change le nom au passage, pour ne pas avoir à taper networkx à chaque fois

Essayons un graphe tout bête :

In [ ]:
G= nx.Graph()  # on forme un graphe, qui est vide au début

On va utiliser de nouveau une notation "avec un point" pour un objet -- on avait déjà vu `L.sort()` quand `L`est une liste, par exemple. C'est très similaire à la notation pour les modules, qui utilise un point aussi.

En l'occurence, voyons `G.add_nodes_from`, où `G` est un graphe:

In [ ]:
G.add_nodes_from([0,1,2,3])  # on a ajouté les sommets 0, 1, 2, 3
# notons que pour networkx la traduction de "sommet" est "node", 
# mais c'est souvent aussi "vertex" (pluriel "vertices")

In [ ]:
# plaçons quelques arêtes (=edge en anglais):
G.add_edge(0,1)
G.add_edge(1,2)
G.add_edge(2,0)
G.add_edge(0,3)

Le module networkx est capable de faire un petit dessin:

In [ ]:
nx.draw(G, with_labels= True)

**Attention**, ça ne marche pas forcément du premier coup, selon votre version de Python, de Jupyter etc. En cas de problème, importer également le module `matplotlib` (dont nous parlerons dans un autre TP).

In [ ]:
import matplotlib

In [ ]:
nx.draw(G, with_labels= True)

Le dessin comporte une part de hasard. Un graphe n'est pas un dessin!

Essayez `with_labels= False` pour voir.

## 3 - Première application

Le but des graphes n'est certainement pas de produire des images. Ce qui va nous intéresser, c'est qu'il y a vraiment beaucoup d'algorithmes sur les graphes qui existent déjà, et qui ont été implémentés par exemple dans networkx. Nous allons pouvoir les utiliser à des fins très diverses, même pour des problèmes qui ne semblent pas immédiatement faire intervenir des graphes.

Voici un exemple. Imaginons qu'on ait une liste `L` d'entiers, et imaginons que cette liste soit énorme, disons des millions d'éléments.

Soit maintenant $p$ un nombre, et supposons que l'on veuille regrouper les éléments de `L` selon leur valeur modulo $p$. Bien sûr on pourrait imaginer l'algorithme suivant: pour chaque $i$ entre $0$ et $p-1$, on regarde tous les éléments de `L` qui sont égaux à $i$ mod $p$, et on met ça dans une liste.

Mais on se dit d'abord que, lorsque l'on a rangé un élément de `L` dans la liste correspondant à un certain $i$, alors il faut le retirer de `L`, puisqu'il est inutile (et très long!) de vérifier si cet élément vaut $j$ mod $p$ pour les $j\ne i$. On voit déjà qu'il va falloir prendre des précautions.

Pour finir, imaginons maintenant que $p$ soit également énorme, plusieurs millions également. Il se pourrait bien que les $x$ mod $p$, pour $x$ dans la liste, ne représentent que peu d'éléments $i$ entre $0$ et $p-1$ -- ils pourraient être tous égaux mod $p$, ou alors $p$ pourrait être beaucoup plus grand que la longueur de la liste `L` !

On a compris maintenant qu'il faudrait prendre un $x$ de `L`, regarder tous les autres éléments de `L`qui sont égaux à $x$ mod $p$, ranger tout ça dans une liste et effacer les éléments en question de `L`, puis recommencer, etc.

Tout ceci est faisable, mais c'est un bon exemple d'opération qui est tellement commune qu'on se dit qu'on doit pouvoir la trouver dans un module. On peut en effet le faire avec `networkx` : imaginons le graphe $G$ dont les sommets sont les éléments de `L`, et avec une arête entre $x$ et $y$ si et seulement si $p$ divise $x-y$. Les "paquets" que l'on se propose de déterminer dans cet exemple sont ce qu'on appelle, en langage des graphes, les *composantes connexes* : les sous-ensembles de sommets qui sont "en un seul morceau". Plus mathématiquement, la composante connexe du sommet $x$ est l'ensemble des sommets que l'on peut atteindre en parcourant un chemin dans $G$ qui part de $x$.

Et bien sûr, `networkx` sait calculer les composantes connexes. Nous pouvons alors résoudre notre problème en seulement quelques lignes.



Commençons par une petite fonction qui crée le graphe $G$ à partir de la liste `L`.

In [ ]:
def graphe_modulo(L,p):
    G= nx.Graph()
    G.add_nodes_from(L)
    N= len(L)
    for i in range(N):
        for j in range(i+1,N):
            x= L[i]
            y= L[j]
            if (x-y)%p == 0:
                G.add_edge(x,y)
    return G

Essayons avec de toutes petites valeurs:

In [ ]:
L= [i for i in range(20)]

In [ ]:
G= graphe_modulo(L, 3)

In [ ]:
nx.draw(G, with_labels= True)

Et le calcul qu'on voulait faire, c'est, en une ligne (!) :

In [ ]:
list( nx.connected_components(G) )

>**Exercice (graphes modulo $p$)**. 
(1) On peut récupérer les arêtes d'un graphe $G$ à l'aide de `G.edges()`; on peut ajouter plusieurs arêtes d'un seul coup à un graphe à l'aide de `G.add_edges_from(liste)`. A l'aide de ces deux méthodes, écrire une fonction `ajoute(G,H)` qui ajoute au graphe $G$ les arêtes du graphe $H$ (ici on suppose que $G$ et $H$ ont les mêmes sommets). Cette fonction modifie $G$, mais ne renvoie rien (pas de `return`). Faire des essais.
>
>(2) Pour `L= [i for i in range(N)]`, avec $N$ de votre choix, et pour différentes valeurs de $p$ et $q$, déterminer le nombre de composantes connexes du graphe $G$ construit par
>
>`G= graphe_modulo(L,p)`
>
>`ajoute(G, graphe_modulo(L,q))`
>
>Emettre une hypothèse. Puis, la démontrer.





## 4 - Deuxième application

Apparemment, il s'agissait à l'origine d'un défi lancé par un journal à ses lecteurs, mais j'ai perdu la référence :

> Quelle est la taille maximale d'un ensemble d'entiers, pris entre 1 et 70, tel que pour toute paire $(a,b)$ de cet ensemble (avec $a\ne b$), la différence $a - b$ n'est pas un carré?

On n'a pas tout de suite l'impression d'un problème sur les graphes. Mais si on pose $S = \{ 1, ..., 70\}$, et si on place une arête entre $i$ et $j$, deux éléments de $S$ avec $i < j$, si $j-i$ n'est pas un carré, alors nous avons un graphe $G$. 

Ce que nous cherchons alors, c'est un ensemble de sommets qui soient tous reliés 2 à 2, de taille maximale. (Prenez le temps de bien digérer ça.)


Or (et c'est toujours comme ça!), le concept existe déjà, et les algorithmes aussi : un tel ensemble, dont les sommets sont tous reliés 2 à 2, est appelé une *clique* du graphe (un [mot français](https://www.larousse.fr/dictionnaires/francais/clique/16581) qui existe aussi en anglais). Et networkx peut nous trouver les cliques maximales (c'est-à-dire les cliques qu'on ne peut pas agrandir, mais c'est malheureusement différent des cliques de taille maximale, il va nous rester un tout petit peu de travail).



In [ ]:
N= 70 # on pourra tester différentes variantes
G= nx.Graph()
G.add_nodes_from(range(1, N+1))

Les carrés qui peuvent intervenir dans les calculs, puisqu'ils sont de la forme $j-i$ avec $i$ et $j$ inférieurs à $N$, doivent eux mêmes être $\le \sqrt N$ :

In [ ]:
from math import sqrt as racine
carres= [x**2 for x in range(int(racine(N))) ]

Plaçons alors les arêtes.

In [ ]:
for i in range(1, N+1):
    for j in range(i+1, N+1):
        if j - i not in carres:
            G.add_edge(i,j)

On peut essayer de dessiner $G$ mais le résultat est décevant :

In [ ]:
nx.draw(G, with_labels= True)

On va maintenant passer en revue les cliques maximales -- données par le module networkx, qui fait le gros du travail pour nous. On en garde une de taille maximale, et c'est fini.

In [ ]:
m= 0           # m est la taille de la plus grande clique que nous ayons trouvée jusqu'à présent
solution= []   # solution est la plus grande clique que nous ayons trouvée jusqu'à présent

for clique in nx.find_cliques(G):  # find_cliques donne la liste des cliques maximales
    if len(clique) > m:
        m= len(clique)
        solution= clique



In [ ]:
solution

In [ ]:
pl= nx.draw(G.subgraph(solution))

>**Exercice ($N=11$).** Pour $N=11$, reprendre le code ci-dessus, afficher toutes les cliques maximales, et vérifier qu'elles n'ont pas toutes le même nombre d'éléments.






*Quelques commentaires.*

A vrai dire, le problème originel était posé pour $N=100$, et pas $N=70$. Avec le code ci-dessus, on n'obtient pas une réponse dans un temps raisonnable. Il existe une bibliothèque de fonctions écrites en C, appelée Cliquer, qui donne une solution presque instantanément :

https://users.aalto.fi/~pat/cliquer.html

C'est peut-être l'occasion de faire de la publicité pour **Sagemath**. Il s'agit d'une distribution Python avec une grosse collection de bibliothèques/modules à vocation mathématique, dont plusieurs ne sont pas écrits en Python, par exemple Cliquer. (Alors que Anaconda, c'est juste Python.) Avec Sagemath, on peut écrire en gros le même code que ci-dessus (et en fait, c'est même un peu plus court), et il va faire appel à Cliquer sans qu'on le voie, pour donner une réponse immédiate.

Nous n'avons pas fait cette série de TPs avec Sagemath parce que, d'une part, il est plus compliqué à installer, et d'autre part, parce que nous voulons en rester aux outils que vous êtes sûrs à 100% d'utiliser si vous continuez vos études (matplotlib et networkx, ainsi que numpy et sympy que nous allons voir, sont vraiment très utilisés, de nos jours).

Allez voir https://www.sagemath.org/.

## 5 - Retour sur le puzzle du TP 2

Comme promis dans le TP 2, nous allons reprendre le puzzle et le résoudre sans "bidouiller", en laissant le programme faire toutes les recherches pour nous. On va traduire les choses avec des graphes, et vous allez finir avec networkx.

Commençons par un copier-coller de l'énoncé :

Ce puzzle est paru en 1994 dans un magazine de supplément offert avec le *Weekend Australian*. 

>Dan est en charge de la promenade de 5 chiens, qui lui ont été confiés par 5 femmes. Seulement, il ne se rappelle plus quel chien appartient à qui, et de plus, il mélange les prénoms des propriétaires. Voici ce dont il est certain.
>
>Le chien de Mme Brown, Loopsie ou Mooksie, n'est pas un terrier. Woopsie, le caniche, n'appartient pas à Mary. Le setter de Marion n'est pas Loopsie. Le basset de Margie s'appelle Smooksie ou Mooksie. Hilary, qui n'est pas Mme Grey, est la maîtresse de Poopsie ou Smooksie. Martha Black n'est pas la maîtresse du dalmatien. Poopsie n'est pas à Mme Grey, mais Mooksie est à Mme White, dont le prénom n'est pas Marion.
>
>Question : sachant que Mme Green est l'une des propriétaires de chien, trouver son prénom, le nom de son chien, et la race de son chien.

(Cette fois-ci, plus d'indication.)

Nous commençons comme dans le TP 1.

In [ ]:
from itertools import product

prenoms= ["Mary", "Marion", "Margie", "Hilary", "Martha"]
noms= ["Brown", "Grey", "Black", "White", "Green"]
races= ["terrier", "caniche", "dalmatien", "setter", "basset"]
chiens= ["Loopsie", "Mooksie", "Smooksie", "Poopsie", "Woopsie"]

comb= [ [p, n, r, c] for p,n,r,c in product(prenoms, noms, races, chiens)]

Comme nous avons appris un peu plus de syntaxe entretemps, on peut être un peu plus élégant:

In [ ]:
implique=  lambda A, B : B or not A
equivalent=lambda A, B : A == B

On va utiliser aussi la commande `all`, qui prend une liste de booléens (True/False) et nous dit s'ils sont tous à True :

In [ ]:
all([True, False, True])

In [ ]:
all([True, True])

In [ ]:
filtre= [ [p,n,r,c] for p,n,r,c in comb if all([
    implique(n=="Brown", c in ["Loopsie", "Mooksie"]),
    implique(n=="Brown", r!= "terrier"),
    equivalent(c == "Woopsie", r == "caniche"),
    implique(c=="Woopsie", p != "Mary"),
    equivalent(r=="setter", p=="Marion"),
    implique(p=="Marion", c!="Loopsie"),
    equivalent(r=="basset", p=="Margie"),
    implique(r=="basset", c in ["Smooksie", "Mooksie"]),
    implique(n=="Grey", not(p=="Hilary")),
    implique(p=="Hilary", c in ["Poopsie", "Smooksie"]),
    equivalent(p=="Martha", n=="Black"),
    implique(p=="Martha", not(r=="dalmatien")),
    implique(n=="Grey", not(c=="Poopsie")),
    equivalent(c=="Mooksie", n=="White"),
    implique(n=="White", not(p=="Marion")) ]) # fin du all([...])
    ] # fin du [ de départ

In [ ]:
len(filtre)

Nous en étions là, avant de commencer les bidouilles. Rappelons que nous appelons "combinaison" un élément tel que, par exemple:

In [ ]:
comb[100]

Une solution du puzzle est alors un ensemble de 5 combinaisons (il y a 5 propriétaires de chiens, donc pour chacune il faut lui attribuer un prénom, un chien et une race) qui ne viole aucune des "règles". Or, en plus des règles que nous avons déjà vues, il y en a une qui est implicite : dans une solution, deux combinaisons n'ont aucun caractère en commun (il y a 5 prénoms différents, 5 noms de famille différents, 5 races etc, et il faut les attribuer tous!). Par exemple

`['Mary', 'Brown', 'terrier', 'Loopsie']`

et

`['Mary', 'Green', 'terrier', 'Mooksie']`

ne peuvent pas apparaître dans la même solution, puisqu'il n'y a qu'une seule femme prénommée Mary, et par ailleurs un seul des chiens est un terrier.

Mézalors, construisons un graphe $G$ sur les sommets $0, ..., 26$, et plaçons une arête entre $i$ et $j$ si `filtre[i]` et `filtre[j]` n'ont aucun caractère en commun. Alors une solution doit former une clique du graphe!

>**Exercice (puzzle, suite et fin).** Finissez le puzzle, en construisant le graphe $G$ et en examinant ses cliques maximales. Vous allez voir au passage que la solution est unique.